### Importing libraries

In [ ]:
from IPython.core.display import display, HTML, Javascript
display(HTML("<style>.container { width:95% !important; }</style>"))

In [ ]:
from vis.jupyter_notebooks.plotters import MultiCostPlotter, SearchResultsPlotter
from vis.jupyter_notebooks.plotters import XRayVideo
from vis.jupyter_notebooks.plotters import move_slider_to_toolbar

In [ ]:
from bokeh.io import push_notebook, show, output_notebook, state
from vehicle.common.proto.decision_debug_pb2 import Decision as DecisionDebug
from data.tools.chum_interactor import ChumInteractor
from data.tools.chum_interactor.interactor import setup_interactors
from vehicle.common.config.vehicle_config_run import get_hardware_config_for_chum_uri

### Preparing the notebook

In [ ]:
from bokeh.io import push_notebook, show, output_notebook, reset_output, state
reset_output()
output_notebook()

### Setting the URIs
Set `chum_uri` to specify the log address. <br>
Set `video_uri` and `start_time` if intend to use the XRay widget. 
The former is the uri to the video associated with this log and it could be retrieved by inspecting the XRay widget html in Argus. 
The latter specifies the start time of the video in global unix time.
<br>


In [ ]:
chum_uri = 'chum://20190830T014725-kitt_09@1567129688.24-1567129733.24'
video_uri = 'https://zoox-argus.s3.us-west-1.amazonaws.com/20190830T014725-kitt_09/kitt_09-1567129645'
start_time = 1567129645

vehicle_config = get_hardware_config_for_chum_uri(chum_uri)
dimensions = vehicle_config.dimensions()

### Creating the plotter widgets, set the layout, and integrate them

Create a set of widgets and a nested list layout to organize the widgets. Pass the layout to the `SearchResultsPlotter` widget and sync all plotters' `notebook_handle`s.

In [ ]:
# Instantiating the XRay video module
xray = XRayVideo(video_uri, start_time)

# Setting up the layout
# Request any plots of interest over different rollouts from SearchResults proto.
# e.g. (x, y), (t, vx), (s, ax), etc.
# combine it with other widgets/views
view_layout = [
    [xray, ('x', 'y')],
    [('s', 'vx'), ('s', 'ax')],
]

# Pass the layout to the last widget and visualize
srp = SearchResultsPlotter(view_layout, vehicle_dimensions=dimensions, pool_cap=100, max_depth=2)
srp.redraw() # This would be equivalent to srp.notebook_handle = show(srp.layout, notebook_handle=True)

### Setting up the interactors and the update functions to supply the data

In [ ]:
TOPIC_DECISION_DEBUG = '/planner/decision/debug'

interactors = setup_interactors(chum_uri, (TOPIC_DECISION_DEBUG, DecisionDebug))
    
interactors[TOPIC_DECISION_DEBUG].select_one('timestamp').select_field('search_results').cb(srp.update_all).display() 
move_slider_to_toolbar()